In [97]:
# Aller chercher les synsets
# Variantes morphologiques
# Enlever les noms des autres commenteux
# Traiter les émoticones

In [98]:
import pandas as pd
import numpy as np
from nltk.corpus import stopwords
from nltk.tokenize import TweetTokenizer
from nltk.parse import CoreNLPParser
import re
import pickle
import emoji

## Tokenisation des commentaires

Utilisation du TweetTokenizer, car il est davantage adapté au contenu des utilisateurs sur les médias sociaux

In [99]:
# Création de l'objet Tokenizer
tok = TweetTokenizer(preserve_case=True)

In [100]:
commentaires_df = pd.read_csv("refined_data/commentaires_df.csv")

In [101]:
commentaires_df.head(10)

Unnamed: 0  comment_id  nested_id                name                   id  \
0           0         1.0          0          Ycf Bullit  ID: 100000615866313   
1           1         2.0          0       Steph Alcazar  ID: 100001175077263   
2           2         3.0          0        Töm Müstäine       ID: 1365879404   
3           3         4.0          0      Pierre Crouzet  ID: 100000270292007   
4           4         4.0          1       Vasanth Toure  ID: 100001494607801   
5           5         4.0          2      Pierre Crouzet  ID: 100000270292007   
6           6         5.0          0    Stéphane Pirnaci  ID: 100008541367302   
7           7         6.0          0        Adil Bennani  ID: 100006432917292   
8           8         7.0          0  Hadrien De Cournon       ID: 1131290552   
9           9         8.0          0        Marwa Larose  ID: 100022577589611   

                  date  likes  \
0  2019-11-09 14:17:13      0   
1  2019-11-09 14:17:34      0   
2  2019-11-09 14:17:51      0   
3  2019-11-09 14:18:06      0   
4  2019-11-09 14:20:57      0   
5  2019-11-09 14:26:37      0   
6  2019-11-09 14:18:51      0   
7  2019-11-09 14:19:03      0   
8  2019-11-09 14:19:09      0   
9  2019-11-09 14:19:38      0   

                                             comment media  \
0                         C'est une blague mdr 🤣🤣🤣🤣🤣   FIG   
1  La seule question c'est de savoir s'il fera pl...   FIG   
2    Romain Debrigode l info du jour qui fait plaise   FIG   
3                                    Vasanth Toure 😍   FIG   
4      Pierre Crouzet Paris n'est pas prêt encore...   FIG   
5      Vasanth Toure le prochain c’est Adrien Rabiot   FIG   
6                                                Mdr   FIG   
7                     moi je propose mamadou sissoko   FIG   
8     Louis Prt Corentin Corman Victor Mdv ah ouais?   FIG   
9              Marier le foot à la mairie est génial   FIG   

                           post_id  
0  5dc7ac7f359e2-10157143278136339  
1  5dc7ac7f359e2-10157143278136339  
2  5dc7ac7f359e2-10157143278136339  
3  5dc7ac7f359e2-10157143278136339  
4  5dc7ac7f359e2-10157143278136339  
5  5dc7ac7f359e2-10157143278136339  
6  5dc7ac7f359e2-10157143278136339  
7  5dc7ac7f359e2-10157143278136339  
8  5dc7ac7f359e2-10157143278136339  
9  5dc7ac7f359e2-10157143278136339

In [102]:
#suppression de la première colonne qui ne sert à rien
del commentaires_df['Unnamed: 0']

## Noms des auteurs

Extraction du nom des auteurs pour chaque commentaire et ses sous-commentaires

In [135]:
names_df = pd.DataFrame(commentaires_df.groupby(['post_id','comment_id'])['name'], columns=['post_comment','list_names'])

In [136]:
names_df['list_names'] = names_df.apply(lambda x: list(set(x['list_names'])), axis=1)

In [137]:
names_df['post_id'] = names_df.apply(lambda x: x['post_comment'][0], axis=1)
names_df['comment_id'] = names_df.apply(lambda x: x['post_comment'][1], axis=1)

In [138]:
del names_df['post_comment']

In [139]:
names_df.head(10)

list_names  \
0                                        [Musta Pha]   
1                            [Pierre-Luc Thibaudeau]   
2                                  [Brandon Fontana]   
3                                  [Maxime Tremblay]   
4                                       [Zahir Idir]   
5                                       [Zahir Idir]   
6                              [Mohammed Elmorshedy]   
7                                      [Ahmed Dades]   
8                                 [Martin Chevalier]   
9  [Maxime Tremblay, Aliza Attias, Étienne Gagné,...   

                          post_id  comment_id  
0  5dc645a8cab5a-2895407083837613         1.0  
1  5dc645a8cab5a-2895407083837613         2.0  
2  5dc645a8cab5a-2895407083837613         3.0  
3  5dc645a8cab5a-2895407083837613         4.0  
4  5dc645a8cab5a-2895407083837613         5.0  
5  5dc645a8cab5a-2895407083837613         6.0  
6  5dc645a8cab5a-2895407083837613         7.0  
7  5dc645a8cab5a-2895407083837613         8.0  
8  5dc645a8cab5a-2895407083837613         9.0  
9  5dc645a8cab5a-2895407083837613        10.0

## Traitement du nom des auteurs dans les textes des commentaires

In [153]:
commentaires_df_names = commentaires_df.merge(names_df)

In [161]:
def list_auteurs_referes(comment,names):
    auteurs_referes = []
    try:
        if len(names) > 0:
            for i in range(len(names)):
                if (comment.find(names[i]) >=0):
                    auteurs_referes.append(names[i])
        return list(set(auteurs_referes))
    except:
        return auteurs_referes

def remove_names(comment,names):
    try:
        if len(names) > 0:
            for i in range(len(names)):
                comment = comment.replace(names[i],'')
        return comment
    except:
        return comment

## Nettoyage des commentaires et traitement des émoticones

In [162]:
commentaires_df_names['auteurs_referes'] = commentaires_df_names.apply(lambda x: str(list_auteurs_referes(x['comment'],x['list_names'])), axis=1)

In [163]:
commentaires_df_names['auteurs_referes']

0                        []
1                        []
2                        []
3         ['Vasanth Toure']
4        ['Pierre Crouzet']
5         ['Vasanth Toure']
6                        []
7                        []
8                        []
9                        []
10                       []
11                       []
12                       []
13                       []
14                       []
15                       []
16                       []
17                       []
18       ['Pierre Trichet']
19                       []
20                       []
21                       []
22          ['Yann Gilles']
23                       []
24                       []
25          ['Yann Gilles']
26              ['Gen Lys']
27                       []
28         ['Jackie Petit']
29                       []
                ...        
37884                    []
37885                    []
37886                    []
37887      ['Luc Pellerin']
37888               

In [164]:
commentaires_df_names['comment_clean'] = commentaires_df_names.apply(lambda x: str(remove_names(x['comment'],x['list_names'])), axis=1)

In [165]:
commentaires_df_names['comment_clean_tok'] = commentaires_df_names.apply(lambda x: tok.tokenize(x['comment_clean']), axis=1)

In [166]:
commentaires_df_names['comment_tok_demojize'] = commentaires_df_names.apply(lambda x: [emoji.demojize(token) for token in x['comment_clean_tok']], axis=1)

In [167]:
del commentaires_df_names['comment_clean']
del commentaires_df_names['comment_clean_tok']

In [168]:
commentaires_df_names

comment_id  nested_id                      name                   id  \
0             1.0          0                Ycf Bullit  ID: 100000615866313   
1             2.0          0             Steph Alcazar  ID: 100001175077263   
2             3.0          0              Töm Müstäine       ID: 1365879404   
3             4.0          0            Pierre Crouzet  ID: 100000270292007   
4             4.0          1             Vasanth Toure  ID: 100001494607801   
5             4.0          2            Pierre Crouzet  ID: 100000270292007   
6             5.0          0          Stéphane Pirnaci  ID: 100008541367302   
7             6.0          0              Adil Bennani  ID: 100006432917292   
8             7.0          0        Hadrien De Cournon       ID: 1131290552   
9             8.0          0              Marwa Larose  ID: 100022577589611   
10            9.0          0                Luca Spada  ID: 100002437345150   
11           10.0          0                 Louis Rey       ID: 1152804021   
12           11.0          0       Mariam Aurelie Koné  ID: 100001068795352   
13           12.0          0                Cedric Cmn  ID: 100036764737328   
14           13.0          0            Olivia Fuentes       ID: 1344277880   
15           14.0          0           Marie Madeleine  ID: 100011469022790   
16           15.0          0            Yohann Lévêque       ID: 1239055989   
17           16.0          0            Pierre Trichet       ID: 1324601288   
18           16.0          1            Martin Trichet       ID: 1210154685   
19           17.0          0             Moumou Soussi       ID: 1607839864   
20           18.0          0          Alexandre Khadir       ID: 1269044664   
21           18.0          1               Yann Gilles  ID: 100004091590140   
22           18.0          2   Claudine Laurent Girard       ID: 1211436111   
23           18.0          3                   Gen Lys  ID: 100009846583553   
24           18.0          4        Sylviane Vaudevire  ID: 100000908768141   
25           18.0          5            Rosette Delion  ID: 100011283737777   
26           18.0          6              Jackie Petit  ID: 100000235001486   
27           18.0          7          Alexandre Khadir       ID: 1269044664   
28           18.0          8             Gerard Brunet  ID: 100022136507326   
29           18.0          9             Gerard Brunet  ID: 100022136507326   
...           ...        ...                       ...                  ...   
37884       168.0          0              Lise Curcuma        ID: 761829665   
37885       169.0          0            Denis Tremblay  ID: 100006112808651   
37886       170.0          0              Luc Pellerin       ID: 1172870365   
37887       170.0          1            Martin Plourde       ID: 1021768060   
37888       171.0          0         Philippe Philippe  ID: 100004395243677   
37889       172.0          0      Monique C. Levasseur  ID: 100001509706168   
37890       173.0          0  Loulou Boudreault-ethier  ID: 100007736719364   
37891       174.0          0           Johanne Richard  ID: 100004469314900   
37892       175.0          0              Lynda Hébert  ID: 100003238117443   
37893       176.0          0          Gaston Pelletier  ID: 100017020566209   
37894       177.0          0              Norm Gilbert        ID: 728106118   
37895       178.0          0      France Martel Patrie  ID: 100000845224363   
37896       179.0          0               Susan Rooke  ID: 100007347765564   
37897       180.0          0           Francois Berube  ID: 100003689235378   
37898       181.0          0          Jonathan Brisson        ID: 512053586   
37899       182.0          0               Karlos Bell  ID: 100004635398883   
37900       183.0          0         Yanick Desrosiers  ID: 100001238092461   
37901       184.0          0          Marielle Cormier       ID: 1004783181   
37902       185.0          0       Marie-Claire Dorais  I